# Risk and Return on Investment in The 10 Biggest Technology Companies in The World & Predictions For The Future

<p> In investment, we all want it will return more money than it costs. But, every investment always be risky - there may be a range of possible outcomes. How does one compare different instrument investments that may deliver similar results on average, but exhibit "**different levels of risks**"? </p>

<p><img style="float: left ; margin: 5px 20px 1px 1px;" width="250" src="sharpe.jpg"></p>

### Introduce Professor William F. Sharpe

<p> He introduced the "<a href="https://web.stanford.edu/~wfsharpe/art/sr/sr.htm"><em>Reward-to-Variability Ratio</em></a>" theory in 1964 which is currently known as the "Sharpe Ratio".</p>
<p> This theory compares the expected return of two investment opportunities and calculates the additional return per unit of risk that an investor could earn by choosing one over the other. In simple terms, this theory looks at the difference in returns of two investments and compares the difference in the mean to the standard deviation (as a measure of risk) of these differences. A higher Sharpe ratio means that the reward will be higher for a given amount of risk.</p>
<p>The Sharpe ratio is one of the most popular risk/return measures in finance because of its ease of use. Toeri has also led Professor Sharpe to win the Nobel Prize in Economics in 1990 for his work on the capital asset pricing model (CAPM)</p>

*"Capital Asset Prices: A Theory of Market Equilibrium under Conditions of Risk (1964)"*

<p>The Sharpe ratio is usually calculated for a portfolio using the risk-free interest rate as a benchmark. However, here we will use stocks instead of portfolios. We will also use stock indices as a benchmark rather than risk-free interest rates because they are both available on a daily frequency (more real-time).</p>

<p>So let's try to find out about the Sharpe ratio of <a href="https://companiesmarketcap.com/tech/largest-tech-companies-by-market-cap/"><em>The 10 Biggest Technology Companies shares</em></a>. As a benchmark, we will use the S&P 500 which measures the performance of 500 largest shares in the US.</p>

### Import Package and Set Enviroment

In [74]:
#import package
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import yfinance as yf
import plotly.graph_objects as go
import cufflinks as cf
from sklearn.preprocessing import MinMaxScaler
from keras.models import Sequential
from keras.layers import Dense, LSTM
from datetime import datetime
import os
os.environ['PYTHONHASHSEED']=str(0)
import tensorflow as tf
import random


#set enviroment
%matplotlib inline
seed_values = 52
os.environ['PYTHONHASHSEED']=str(0)
tf.random.set_seed(seed_values)
np.random.seed(seed_values)
random.seed(seed_values)
cf.set_config_file(theme='pearl', world_readable=False, offline=True)

### Download 10 Big Tech Companies Stock Price from Yahoo! Finance's API

<p> Based on <a href="https://companiesmarketcap.com/tech/largest-tech-companies-by-market-cap/"><em>Companiesmarketcap Website</em></a>, The world's top 10 technology companies are : </p>

- Apple (USA)
- Microsoft (USA)
- Google (USA)
- Amazon (USA)
- Tesla (USA)
- Meta Platforms (USA)
- Taiwan Semiconductor Manufacturing Company (Taiwan)
- Tencent (China)
- Nvidia (USA)
- Alibaba (China)

<p> Here we will use stock prices from the past 5 years. </p>

In [75]:
#List of Top 10 Tech Company
company_list = ['AAPL','MSFT','GOOG','AMZN','TSLA','META','TSM','TCEHY','NVDA','BABA']

#Set start and end of stock price that will download
end = datetime.now()
start = datetime(end.year-5,end.month,end.day)

#Download for every stock price
alldata = yf.download(company_list,start,end)
alldata.head()

[*********************100%***********************]  10 of 10 completed


Adj Close                                                \
                 AAPL       AMZN        BABA       GOOG        META   
Date                                                                  
2017-09-05  38.456120  48.263500  169.919998  46.422501  170.720001   
2017-09-06  38.415787  48.389999  168.139999  46.390499  172.089996   
2017-09-07  38.261566  48.973499  170.479996  46.797501  173.210007   
2017-09-08  37.637554  48.294998  169.000000  46.325001  170.949997   
2017-09-11  38.318516  48.897999  174.059998  46.453999  173.509995   

                                                                   ...  \
                 MSFT       NVDA      TCEHY       TSLA        TSM  ...   
Date                                                               ...   
2017-09-05  69.167618  41.053204  40.321800  23.306000  32.222637  ...   
2017-09-06  68.970291  41.028465  41.139473  22.968666  32.589893  ...   
2017-09-07  69.853561  41.218990  40.784824  23.374001  32.825996  ...   
2017-09-08  69.515289  40.503872  40.213436  22.893333  32.791012  ...   
2017-09-11  70.248207  41.817806  42.085213  24.246000  33.088322  ...   

               Volume                                                    \
                 AAPL      AMZN      BABA      GOOG      META      MSFT   
Date                                                                      
2017-09-05  117874000  57664000  14943600  26528000  13210900  21556000   
2017-09-06   86606800  42598000  19988300  30554000  13906300  16535800   
2017-09-07   87714000  51336000  15141900  24254000  18049500  17471200   
2017-09-08  114446000  52106000  12345300  20230000  10998500  14703800   
2017-09-11  126323200  43734000  18257900  25340000  12372000  17910400   

                                                   
                NVDA    TCEHY       TSLA      TSM  
Date                                               
2017-09-05  69536400  2465700   57526500  7123000  
2017-09-06  39767200  1277300   61371000  4187700  
2017-09-07  35286800  1343500   63588000  3597500  
2017-09-08  49885600  1271100   48952500  5581800  
2017-09-11  56744400  1554600  115006500  6920100  

[5 rows x 60 columns]

### Daily Closing Price
<p> The dataframe above shows the stock price at the time of opening, high, low, closing, adjusted closing, and daily trading volume. But, we only need adjusted closing price column for every company stock. So, we will create a pivot table for slicing adj close for each company every day.</p>

In [76]:
#Create Pivot table
stock = alldata['Adj Close']
stock

AAPL        AMZN        BABA        GOOG        META  \
Date                                                                     
2017-09-05   38.456120   48.263500  169.919998   46.422501  170.720001   
2017-09-06   38.415787   48.389999  168.139999   46.390499  172.089996   
2017-09-07   38.261566   48.973499  170.479996   46.797501  173.210007   
2017-09-08   37.637554   48.294998  169.000000   46.325001  170.949997   
2017-09-11   38.318516   48.897999  174.059998   46.453999  173.509995   
...                ...         ...         ...         ...         ...   
2022-08-29  161.380005  129.789993   96.599998  110.339996  159.169998   
2022-08-30  158.910004  128.729996   93.839996  109.910004  157.160004   
2022-08-31  157.220001  126.769997   95.410004  109.150002  162.929993   
2022-09-01  157.960007  127.820000   93.709999  110.550003  165.360001   
2022-09-02  155.809998  127.510002   91.800003  108.680000  160.320007   

                  MSFT        NVDA      TCEHY        TSLA        TSM  
Date                                                                  
2017-09-05   69.167618   41.053204  40.321800   23.306000  32.222637  
2017-09-06   68.970291   41.028465  41.139473   22.968666  32.589893  
2017-09-07   69.853561   41.218990  40.784824   23.374001  32.825996  
2017-09-08   69.515289   40.503872  40.213436   22.893333  32.791012  
2017-09-11   70.248207   41.817806  42.085213   24.246000  33.088322  
...                ...         ...        ...         ...        ...  
2022-08-29  265.230011  158.009995  40.750000  284.820007  82.849998  
2022-08-30  262.970001  154.679993  40.000000  277.700012  82.790001  
2022-08-31  261.470001  150.940002  41.299999  275.609985  83.349998  
2022-09-01  260.399994  139.369995  41.180000  277.160004  81.639999  
2022-09-02  256.059998  136.470001  41.419998  270.209991  80.900002  

[1259 rows x 10 columns]

### Visualization & Summarize Daily Stock Price

<p>Let's visualize all data stock price in one graph, so we get better understand what we're dealing with.</p>

In [77]:
stock.iplot(title='Top 10 Big Tech Companies Stock Prices', xTitle='Dates',yTitle='Adjusted Close Prices')

#### Highest Stock Price Right Now

In [78]:
highest = stock.tail(1).sort_values(by=stock.index[-1],ascending=False,axis=1)
display(highest)

print(f'Here, we can see {highest.columns[0]}, {highest.columns[1]} and {highest.columns[2]} have the highest stock price right now.')
print('But, will the 3 companies provide the highest returns as well?')

TSLA        MSFT        META        AAPL        NVDA  \
Date                                                                     
2022-09-02  270.209991  256.059998  160.320007  155.809998  136.470001   

                  AMZN    GOOG       BABA        TSM      TCEHY  
Date                                                             
2022-09-02  127.510002  108.68  91.800003  80.900002  41.419998

Here, we can see TSLA, MSFT and META have the highest stock price right now.
But, will the 3 companies provide the highest returns as well?


### S&P 500 as Benchmark

In [79]:
#Download S&P 500 Stock Price
SP500 = yf.download('^GSPC',start,end)

#Slicing S&P 500 Dataframe for only Adjusted close column
benchmark = SP500.filter(['Adj Close'])
benchmark

[*********************100%***********************]  1 of 1 completed


Adj Close
Date                   
2017-09-05  2457.850098
2017-09-06  2465.540039
2017-09-07  2465.100098
2017-09-08  2461.429932
2017-09-11  2488.110107
...                 ...
2022-08-29  4030.610107
2022-08-30  3986.159912
2022-08-31  3955.000000
2022-09-01  3966.850098
2022-09-02  3924.260010

[1259 rows x 1 columns]

In [80]:
#Plot Bencmark
benchmark.iplot(title='S&P 500 Stock Prices', xTitle='Dates',yTitle='Adjusted Close Prices',color='green')

### Calculate The Daily Return of Price Stock

The Sharpe ratio uses the difference in returns of all considered investment opportunities.

However, our data show the daily price of each investment, not the daily return. To calculate the daily return, we need to calculate the percentage change in value from one day to the next. We'll also take a look at the summary statistics because these will become our inputs as we calculate the Sharpe Ratio.

#### Daily Stock Return

In [81]:
#Calculating daily returns from daily stock price changes
stock_return = stock.pct_change()

#Plot daily returns
stock_return.iplot(title='Daily Stock Return',xTitle='Dates',yTitle='Return (%)')

#### Daily Benchmark Return

In [82]:
#Calculating daily returns from daily benchmark price changes
benchmark_return = benchmark['Adj Close'].pct_change()

#Plot daily returns
benchmark_return.iplot(title='S&P 500 Daily Return',xTitle='Dates',yTitle='Return (%)',color='green')

### Calculating Excess Returns for All Companies with S&P 500

<p>Next, we need to calculate the relative performance of all stocks vs. the S&P 500 benchmark. This is calculated as the difference in returns between <code>Stock return</code> and <code>Benchmark return</code> for each day.</p>

In [83]:
#Calculate the difference in daily returns
excess_return = stock_return.sub(benchmark_return,axis=0)

#Plot daily excess returns
excess_return.iplot(title='Daily Excess Return',xTitle='Dates',yTitle='Return (%)')

#Generate descriptive statistics of excess_return
excess_return.describe()

AAPL         AMZN         BABA         GOOG         META  \
count  1258.000000  1258.000000  1258.000000  1258.000000  1258.000000   
mean      0.000859     0.000547    -0.000548     0.000394    -0.000184   
std       0.012748     0.016504     0.025852     0.011687     0.019570   
min      -0.074851    -0.104210    -0.136958    -0.077917    -0.239510   
25%      -0.006126    -0.007417    -0.013348    -0.005585    -0.008762   
50%       0.000476    -0.000121    -0.000980     0.000031    -0.000372   
75%       0.007386     0.007945     0.011318     0.006353     0.008496   
max       0.097018     0.130202     0.345256     0.097098     0.151189   

              MSFT         NVDA        TCEHY         TSLA          TSM  
count  1258.000000  1258.000000  1258.000000  1258.000000  1258.000000  
mean      0.000757     0.001001    -0.000091     0.002296     0.000496  
std       0.010358     0.024168     0.023903     0.035917     0.016271  
min      -0.036688    -0.189782    -0.102696    -0.183009    -0.069563  
25%      -0.005060    -0.012583    -0.012739    -0.015891    -0.008813  
50%       0.000510     0.000274    -0.001110     0.001226    -0.000015  
75%       0.005694     0.013890     0.011465     0.019082     0.009054  
max       0.056046     0.116241     0.311964     0.191694     0.119127

## Compute The Sharpe Ratio

#### 1. Calculate The Average of *Excess Returns*

<p>This tells us how much more or less the investment yields per day compared to the benchmark.</p>

In [84]:
#Calculating the average of excess returns
avg_excess_return = excess_return.mean()

#Plot the average excess returns
avg_excess_return.iplot(kind='bar',title='Mean of the Return Difference',yTitle='Mean Return (%)',xTitle='Company',color='darkorange')

In [85]:
print(f'It looks like there was quite a bit of a difference between average daily returns for all Companies. But, {avg_excess_return.sort_values(ascending=False).index[0]} mean return it\'s most higher')

It looks like there was quite a bit of a difference between average daily returns for all Companies. But, TSLA mean return it's most higher


#### 2. Calculate The Standard Deviation of The *Excess Returns*

<p>Next, we calculate the standard deviation of the excess_returns. This shows us the amount of risk an investment in the stocks implies as compared to an investment in the S&P 500.</p>

In [86]:
#Calculating the standard deviation of excess return
std_excess_return = excess_return.std()

#Plot the standard deviation of excess return
std_excess_return.iplot(kind='bar',title='Standard Deviation of the Return Difference',xTitle='Company',yTitle='Standard Deviation (%)',color='darkcyan')

#### 3. Calculate the Sharpe ratio
Ratio of *Average Excess Returns* and *Standard Deviation of Excess Returns*.

Indicates how much more (or less) return the investment opportunity under consideration yields per unit of risk.

The Sharpe Ratio is often *annualized* by multiplying it by the square root of the number of periods. We have used daily data as input, so we'll use the square root of the number of trading days (5 days, 52 weeks, minus a few holidays, for 5 years): √(252*5)

In [87]:
#Calculate the daily sharpe ratio
daily_sharpe_ratio = avg_excess_return.div(std_excess_return)

#Annualize the sharpe ratio
annual_factor = np.sqrt(252*5)
annual_sharpe_ratio = daily_sharpe_ratio.mul(annual_factor)

#Plot the annualized sharpe ratio 
annual_sharpe_ratio.iplot(kind='bar',title='Stocks vs S&P 500',xTitle='Company',yTitle='Annual Sharpe Ratio',color='bluepurple')

#Show the top 3 sharpe ratio
top_ratio = annual_sharpe_ratio.sort_values(ascending=False)[:3]
print('Top 3 Companies with Highest Sharpe Ratio')
print(top_ratio)

Top 3 Companies with Highest Sharpe Ratio
MSFT    2.595507
AAPL    2.392394
TSLA    2.269232
dtype: float64


### Conclusion

Since 5 years ago until now, The 3 Tech Companies above have the highest sharpe ratio among the top 10 Tech Companies in the World. This means that investments in the three companies above will yield higher returns per unit of risk. In other words, investing in 3 Tech Companies above would be more attractive.

When faced with investment alternatives that offer both different returns and risks, the Sharpe Ratio helps to make a decision by adjusting the returns by the differences in risk and allows an investor to compare investment opportunities on equal terms, that is, on an 'apples-to-apples' basis.

# Predicting Price Stock of Companies with Highest Sharpe Ratio

In [88]:
#Slicing the company with highest sharpe ratio
topcomp = str(top_ratio.index[0])
print('Company with highest sharpe ratio:',topcomp)

#Download dataset Stock Top Company
print(f'Download {topcomp} stock price')
data = yf.download(topcomp,start,end)

Company with highest sharpe ratio: MSFT
Download MSFT stock price
[*********************100%***********************]  1 of 1 completed


In [89]:
qf=cf.QuantFig(data,title=f'{topcomp} Stock Price',legend='top',name='Price',yTitle='Price ($)')
qf.add_sma([7,30],color=['blue','orange'],legendgroup=True)
qf.add_volume(up_color='green', down_color='red')
qf.iplot(up_color='green', down_color='red')

In [90]:
dataset = data.filter(['Adj Close']).values
training_data_len = int(np.ceil( len(dataset) * .95 ))
dataset

array([[ 69.1676178 ],
       [ 68.97027588],
       [ 69.8535614 ],
       ...,
       [261.47000122],
       [260.3999939 ],
       [256.05999756]])

In [91]:
scaler = MinMaxScaler(feature_range=(0,1))
scaled_data = scaler.fit_transform(dataset)

scaled_data

array([[1.20895090e-03],
       [4.83546708e-04],
       [3.73039374e-03],
       ...,
       [7.08088445e-01],
       [7.04155232e-01],
       [6.88201948e-01]])

In [92]:
train_data = scaled_data[:training_data_len, :]

x_train = []
y_train = []

for i in range(60, len(train_data)):
    x_train.append(train_data[i-60:i, 0])
    y_train.append(train_data[i, 0])
        
# Convert the x_train and y_train to numpy arrays 
x_train, y_train = np.array(x_train), np.array(y_train)

# Reshape the data
x_train = np.reshape(x_train, (x_train.shape[0], x_train.shape[1], 1))

In [93]:
# Build the LSTM model
model = Sequential()
model.add(LSTM(128, return_sequences=True, input_shape= (x_train.shape[1], 1)))
model.add(LSTM(64, return_sequences=False))
model.add(Dense(25))
model.add(Dense(1))

# Compile the model
model.compile(optimizer='adam', loss='mean_squared_error')

# Train the model
model.fit(x_train, y_train, batch_size=1, epochs=10)

Epoch 1/10
1137/1137 [==============================] - 27s 21ms/step - loss: 0.0018
Epoch 2/10
1137/1137 [==============================] - 30s 27ms/step - loss: 0.0010
Epoch 3/10
1137/1137 [==============================] - 42s 37ms/step - loss: 6.5421e-04
Epoch 4/10
1137/1137 [==============================] - 36s 32ms/step - loss: 5.5469e-04
Epoch 5/10
1137/1137 [==============================] - 28s 24ms/step - loss: 5.9825e-04
Epoch 6/10
1137/1137 [==============================] - 28s 25ms/step - loss: 4.7737e-04
Epoch 7/10
1137/1137 [==============================] - 27s 24ms/step - loss: 4.9580e-04
Epoch 8/10
1137/1137 [==============================] - 28s 24ms/step - loss: 5.7083e-04
Epoch 9/10
1137/1137 [==============================] - 28s 25ms/step - loss: 4.5111e-04
Epoch 10/10
1137/1137 [==============================] - 27s 24ms/step - loss: 4.0462e-04


In [182]:
# Create the testing data set
test_data = scaled_data[training_data_len - 60: , :]
# Create the data sets x_test and y_test
x_test = []
y_test = dataset[training_data_len:, :]
for i in range(60, len(test_data)):
    x_test.append(test_data[i-60:i+1, 0])
    
# Convert the data to a numpy array
x_test = np.array(x_test)

# Reshape the data
x_test = np.reshape(x_test, (x_test.shape[0], x_test.shape[1], 1 ))

# Get the models predicted price values 
predictions = model.predict(x_test)
predictions = scaler.inverse_transform(predictions)

2/2 [==============================] - 1s 19ms/step


In [183]:
# Plot the data
train = data.filter(['Adj Close'])[:training_data_len+1]
valid = data.filter(['Adj Close'])[training_data_len:]
valid['Predictions'] = predictions

# Visualize the data
fig = go.Figure([
  go.Scatter(name='Training',x=train.index,y=train['Adj Close'],fill='tozeroy',showlegend=True),
  go.Scatter(name='Validations',x=valid.index,y=valid['Adj Close'],fill='tozeroy',showlegend=True),
  go.Scatter(name='Predictions',x=valid.index,y=valid['Predictions'],fill='tozeroy',showlegend=True)
  ])
fig.update_layout(
  xaxis_title='Dates',
  yaxis_title='Price ($)',
  title=f'Model {topcomp} Stock Price Predictions')

fig.show()

In [185]:
# Show the valid and predicted prices
valid

Adj Close  Predictions
Date                               
2022-06-07  271.922821   271.505066
2022-06-08  269.837250   270.440948
2022-06-09  264.229156   265.527649
2022-06-10  252.454147   254.991272
2022-06-13  241.746857   244.563080
...                ...          ...
2022-08-29  265.230011   266.984924
2022-08-30  262.970001   264.673309
2022-08-31  261.470001   263.203125
2022-09-01  260.399994   262.120056
2022-09-02  256.059998   258.314728

[62 rows x 2 columns]

In [188]:
from sklearn.metrics import r2_score,mean_absolute_error,mean_squared_error
score = [
  round(r2_score(valid['Adj Close'], valid['Predictions']),3),
  round(mean_absolute_error(valid['Adj Close'], valid['Predictions']),3),
  round(mean_squared_error(valid['Adj Close'], valid['Predictions']),3)]

print('Result')
pd.DataFrame(score,index=['Score','MAE','MSE']).T

Result


Score    MAE    MSE
0  0.993  0.858  1.322

In [195]:
model.summary()
model.save('model.hdf5')

Model: "sequential_5"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm_10 (LSTM)              (None, 60, 128)           66560     
                                                                 
 lstm_11 (LSTM)              (None, 64)                49408     
                                                                 
 dense_10 (Dense)            (None, 25)                1625      
                                                                 
 dense_11 (Dense)            (None, 1)                 26        
                                                                 
Total params: 117,619
Trainable params: 117,619
Non-trainable params: 0
_________________________________________________________________


In [196]:
model.save('model')

INFO:tensorflow:Assets written to: model/assets


INFO:tensorflow:Assets written to: model/assets
